In [1]:
import pandas as pd
import nibabel as nib
import numpy as np
import math
import xml.etree.ElementTree as ET
from tqdm import tqdm

In [ ]:
class queryBrainnetomeROI:
    """
    Class queryBrainnetomeROI provides methods by which you can accomplish the following:
    - Given ROI number get [Lobe, Gyrus, Region and MNI Coordinates] using queryDict(ROI_number) or queryDict([ROI_numbers])
    - Given MNI coordinates get [Lobe, Gyrus, Region and MNI Coordinates] using getAtlasRegions([x,y,z])
    Usage:
    >>> atlas_path = 'BNA-maxprob-thr0-1mm.nii.gz' # path to the atlas file
    >>> atlasRegionsDescrpPath = 'brainnetomeAtlas/BNA_subregions_machineReadable.xlsx' # path to ROI description xlsx
    >>> q = queryBrainnetomeROI(atlas_path, atlasRegionsDescrpPath)
    >>> q.queryDict(246)
    [array(['Subcortical Nuclei', 'Tha, Thalamus',
        'Tha_lPFtha, lateral pre-frontal thalamus', '13, -16, 7 '],
       dtype=object)]
    """
    def __init__(self, atlas_path, atlasRegionsDescrpPath , prob = False ):
        self.atlas_path = atlas_path
        
        self.prob = prob
        
        
        _atlas = nib.load(self.atlas_path)
        self.atlas = _atlas.get_data()
        
        print('Atlas read')
        if _atlas.header['pixdim'][1] == 2:
            self.pixdim = 2
#             x,y,z = self.MNI2XYZ2mm(coordMni)
        elif _atlas.header['pixdim'][1] == 1:
            self.pixdim = 1
#             x,y,z = self.MNI2XYZ1mm(coordMni)
        else:
            raise Exception('Unknown Pixel Dimension', _atlas.header['pixdim'][1] )

        print('checked Pixel dimension')
            
        self.numSeeds = None
        self.atlasRegionsDescrpPath = atlasRegionsDescrpPath
            

    def MNI2XYZ1mm(self, mni):
        x =  - mni[0] + 90
        y = mni[1] + 126
        z = mni[2] + 72
        return [x,y,z]
    
    def MNI2XYZ2mm(self, mni):   
        x =  math.floor((- mni[0] + 90)/2.0)
        y = math.floor((mni[1] + 126)/2.0)
        z = math.floor((mni[2] + 72)/2.0)
        return [x,y,z]
    
    def brainnetomeQuery(self):
        """
        Extract the region names from excel file and creates a dictionary i.e. key value pair
        where Key is the ROI number and Value is the list of [Lobe, Gyrus, Region and MNI Coordinates] 
        of the query ROI Number.
        
        """
#         atlas = nib.load(self.atlas_path).get_data()
        df = pd.read_excel(self.atlasRegionsDescrpPath)

        if self.prob:
            self.numSeeds = self.atlas.shape[3]
        else:
            self.numSeeds = int(np.max(self.atlas))

        df = df.as_matrix(['Lobe','Gyrus','Label ID.L', 'Label ID.R','Left and Right Hemisphere','Unnamed: 5', 'lh.MNI(X,Y,Z)', 'rh.MNI(X,Y,Z)'])
        seedInfo = np.empty((self.numSeeds + 1, 5),dtype=object)

        for lobe, gyrus, i,j,region,label,lcoord,rcoord in df:
            seedInfo[i,:] = i,lobe, gyrus, region.split('_')[0] + '_' + label, lcoord
            seedInfo[j,:] = j,lobe, gyrus, region.split('_')[0] + '_' + label, rcoord

   
        # Create a dictionary of seedInfo so that it can be accessed by roi number

        ROI_dictionary = {}
        for i in seedInfo[1:]:
            ROI_dictionary[i[0]] = i[1:]
            
        return ROI_dictionary



    def queryDict(self, lis): # lis: List that contains ROI numbers (1 to 246)
        """
        Used yhe dicrionary created by self.brainnetomeQuery() and ... 
        Returns the list of [Lobe, Gyrus, Region and MNI Coordinates] of the query ROI Number 
        """
        
        ROI_dictionary = self.brainnetomeQuery()
        return_regions = []
        
        # If input is a list of ROI numbers
        if isinstance(lis,list): 
            for i in lis:
                try: return_regions.append(ROI_dictionary[i])
                except KeyError: 
                    # returns List of None if ROI number is not found. ROI = [1,246]
                    return_regions.append([None,None,None,None])
                    
        # If input is just a single ROI number
        else:
            i = lis
            try: return_regions.append(ROI_dictionary[i])
            except KeyError:
                return_regions.append([None,None,None,None])
                
        
        return return_regions
    
    def getAtlasRegions(self, coordMni):
        """
        Converts the MNI coordinates to image coordinates by using MNI2XYZ2mm() or MNI2XYZ1mm()
        It calls self.queryDict() in the background
        Returns the list of [Lobe, Gyrus, Region and MNI Coordinates] of the query MNI Coordinate.
        """
#         _atlas = nib.load(self.atlas_path)
#         atlas = _atlas.get_data()
#         if _atlas.header['pixdim'][1] == 2:
        if self.pixdim == 2:
            x,y,z = self.MNI2XYZ2mm(coordMni)
#         elif _atlas.header['pixdim'][1] == 1:
        elif self.pixdim == 1:
            x,y,z = self.MNI2XYZ1mm(coordMni)
#         else:
#             raise Exception('Unknown Pixel Dimension', _atlas.header['pixdim'][1] )
        if self.prob == False:
            roiNumber = self.atlas[x,y,z]
        else:
            vec_of_prob = self.atlas[x,y,z,:]
            roiNumber = np.argmax(vec_of_prob) + 1 # [1 ... num_roi's]
            max_prob =  vec_of_prob[roiNumber]
            if max_prob == 0: # # Coordinate is outside the atlas
                itr = [0,1,-1,2,-2,3,-3]
                roiNumber, final_coord, final_itr = self.get_neighbouring_coordinates(x,y,z,itr)
                
                                    

        lobe, gyrus, roiName, _ = self.queryDict(roiNumber)[0]
        return int(roiNumber),lobe, gyrus, roiName
    
    def get_neighbouring_coordinates(self,x,y,z,itr):
        final_coord = [x,y,z]
        old_dist = float('Inf')
        final_itr = [0,0,0]
        final_roi = 0
        for xi in itr:
            for yi in itr:
                for zi in itr:
                    vec_of_prob = self.atlas[x-xi,y-yi,z-zi,:]
                    roiNumber = np.argmax(vec_of_prob) + 1 # [1 ... num_roi's]
                    max_prob =  vec_of_prob[roiNumber - 1]
#                     print('coord',x-xi,y-yi,z-zi)
#                     print('MAx_prob',max_prob)
                    if max_prob != 0: # the max roi lies inside the atlas
                        dist = abs(xi) +  abs(yi)  + abs(zi)
                        if dist < old_dist or final_itr == [0,0,0]:
#                             print('old_dist',old_dist)
                            old_dist = dist
                            final_coord = [x-xi, y-yi, z-zi]
                            final_itr = [xi,yi,zi]
                            final_roi = roiNumber

        return final_roi, final_coord, final_itr
                                    
    
  


In [3]:
# del q
# atlas_path = 'brainnetomeAtlas/BNA-maxprob-thr0-1mm.nii.gz'
atlas_path = 'brainnetomeAtlas/BNA-prob-2mm.nii.gz'
# atlasRegionsDescrpPath = '/home/varun/Projects/fmri/Autism-Connectome-Analysis-brain_connectivity/atlas/BNA_subregions.xlsx'
atlasRegionsDescrpPath = 'brainnetomeAtlas/BNA_subregions_machineReadable.xlsx'
q = queryBrainnetomeROI(atlas_path,atlasRegionsDescrpPath, True)

Atlas read
checked Pixel dimension


NameError: name 'q' is not defined

In [46]:
a = nib.load(atlas_path).get_data()

In [51]:
del a

In [59]:
q.queryDict(246)

[array(['Subcortical Nuclei', 'Tha, Thalamus',
        'Tha_lPFtha, lateral pre-frontal thalamus', '13, -16, 7 '],
       dtype=object)]

In [4]:
q.queryDict(246) # Returns Lobe, Gyrus, Region and MNI Coordinates of the query ROI Number

[array(['Subcortical Nuclei', 'Tha, Thalamus',
        'Tha_lPFtha, lateral pre-frontal thalamus', '13, -16, 7 '],
       dtype=object)]

In [57]:
q.getAtlasRegions([13,-16,7])

(246,
 'Subcortical Nuclei',
 'Tha, Thalamus',
 'Tha_lPFtha, lateral pre-frontal thalamus')

In [60]:
itr = [0,1,-1,2,-2,3,-3]
q.get_neighbouring_coordinates(-45,30,67,itr)

(147, [-45, 30, 66], [0, 0, 1])

In [64]:
np.array([[1,2,3,4],[5,6,7,8]])[-1,1]

6

In [6]:
class _queryAtlas:
    '''
    atlasPaths : List of paths to the nii files to be considered in order of preference
    atlasLabelsPaths : List of paths to the xml files containing labels to be considered in order of preference 
    coord : List [x,y,z] of MNI coordinates
    Usage:
    >>> atlasPaths1  = ['hoAtlas/HarvardOxford-cort-maxprob-thr25-2mm.nii.gz',\
               'hoAtlas/HarvardOxford-sub-maxprob-thr25-2mm.nii.gz',
               'cerebellumAtlas/Cerebellum-MNIflirt-maxprob-thr25-1mm.nii.gz']
    >>> atlasLabelsPaths1 = ['hoAtlas/HarvardOxford-Cortical.xml','hoAtlas/HarvardOxford-Subcortical.xml',\
                    'cerebellumAtlas/Cerebellum_MNIflirt.xml']
    >>> q1 = queryAtlas(atlasPaths1,atlasLabelsPaths1)
    >>> q1.getAtlasRegions([-6,62,-2])
    (1, 'Frontal Pole', 0) 
    

    
    '''
    def __init__(self,atlasPaths,atlasLabelsPaths):
        self.atlasPaths = atlasPaths
        self.atlasLabelsPaths = atlasLabelsPaths
        
    
    def MNI2XYZ1mm(self, mni):
        x =  - mni[0] + 90
        y = mni[1] + 126
        z = mni[2] + 72
        return [x,y,z]
    
    def MNI2XYZ2mm(self, mni):   
        x =  math.floor((- mni[0] + 90)/2.0)
        y = math.floor((mni[1] + 126)/2.0)
        z = math.floor((mni[2] + 72)/2.0)
        return [x,y,z]
    
    def roiName(self, atlasLabelsPath, roiNum):
        '''
        Takes as input the Atlas labels path and ROI Number and outputs the ROI name for that atlas
        '''
        atlasDict = {}
        root = ET.parse(atlasLabelsPath).getroot()
        elem = root.find('data')
        for regionRow in elem.getchildren():
            # roiNumber  = int(regionRow.items()[2][1]) + 1 .items() gives the items in arbitary order so indexing changes
            roiNumber = int(regionRow.get(key='index')) + 1
            roiName = regionRow.text
            atlasDict[roiNumber] = roiName

        return atlasDict[roiNum]
     
    def getAtlasRegions(self, coordMni):
        '''
        Takes as input MNI coordinates and returns a tuple (ROI_number, Region_name, Atlas_index_used)
        '''
        roiNumber = None
        roiName = None
        
        atlasIndex = 0
        # Enumerates over all the given atlases and stops when the region is found in some atlas. 
        for index,atlasPath in enumerate(self.atlasPaths):
            if roiNumber == None:
                _atlas = nib.load(atlasPath)
                atlas = _atlas.get_data()
                if _atlas.header['pixdim'][1] == 2:
                    x,y,z = self.MNI2XYZ2mm(coordMni)
                elif _atlas.header['pixdim'][1] == 1:
                    x,y,z = self.MNI2XYZ1mm(coordMni)
                else:
                    raise Exception('Unknown Pixel Dimension', _atlas.header['pixdim'][1] )

                
                roiNumber = atlas[x,y,z]
                if roiNumber != 0:
                    roiName = self.roiName(self.atlasLabelsPaths[index], roiNumber)
                    
                    roiName  = roiName.strip()
                    if roiName == 'Right Cerebral White Matter' or roiName == 'Left Cerebral White Matter'\
                    or roiName == 'Left Cerebral Cortex' or roiName == 'Right Cerebral Cortex':
                        #print('ROI Name is %s at atlas index %s'% (roiName, atlasIndex))
                        
                        roiNumber = None
                        atlasIndex = atlasIndex + 1
                        continue
                
                else:
                    roiNumber = None
                    atlasIndex = atlasIndex + 1
                    

        if roiNumber == None:
            roiNumber, roiName, atlasIndex = 0, None, None
            
        return int(roiNumber), roiName, atlasIndex

In [51]:
# Improved
class queryAtlas:
    '''
    atlasPaths : List of paths to the nii files to be considered in order of preference
    atlasLabelsPaths : List of paths to the xml files containing labels to be considered in order of preference 
    coord : List [x,y,z] of MNI coordinates
    Usage:
    >>> atlasPaths1  = ['hoAtlas/HarvardOxford-cort-maxprob-thr25-2mm.nii.gz',\
               'hoAtlas/HarvardOxford-sub-maxprob-thr25-2mm.nii.gz',
               'cerebellumAtlas/Cerebellum-MNIflirt-maxprob-thr25-1mm.nii.gz']
    >>> atlasLabelsPaths1 = ['hoAtlas/HarvardOxford-Cortical.xml','hoAtlas/HarvardOxford-Subcortical.xml',\
                    'cerebellumAtlas/Cerebellum_MNIflirt.xml']
    >>> q1 = queryAtlas(atlasPaths1,atlasLabelsPaths1)
    >>> q1.getAtlasRegions([-6,62,-2])
    (1, 'Frontal Pole', 0) 
    

    
    '''
    def __init__(self,atlasPaths,atlasLabelsPaths, prob = False):
        self.atlasPaths = atlasPaths
        self.atlasLabelsPaths = atlasLabelsPaths
        self.prob = prob
        self.itr = [0,1,-1,2,-2,3,-3]
        self.atlas_list = []
        self.pixdim_list = []
    
        for index,atlasPath in enumerate(self.atlasPaths):
        
            _atlas = nib.load(atlasPath)
            atlas = _atlas.get_data()

            self.atlas_list.append(atlas)


            print('Atlas read')
            if _atlas.header['pixdim'][1] == 2:
                pixdim = 2
    #             x,y,z = self.MNI2XYZ2mm(coordMni)
            elif _atlas.header['pixdim'][1] == 1:
                pixdim = 1
    #             x,y,z = self.MNI2XYZ1mm(coordMni)
            else:
                raise Exception('Unknown Pixel Dimension', _atlas.header['pixdim'][1] )

            self.pixdim_list.append(pixdim)
            print('checked Pixel dimension')

        
    
    def MNI2XYZ1mm(self, mni):
        x =  - mni[0] + 90
        y = mni[1] + 126
        z = mni[2] + 72
        return [x,y,z]
    
    def MNI2XYZ2mm(self, mni):   
        x =  math.floor((- mni[0] + 90)/2.0)
        y = math.floor((mni[1] + 126)/2.0)
        z = math.floor((mni[2] + 72)/2.0)
        return [x,y,z]
    
    def roiName(self, atlasLabelsPath, roiNum):
        '''
        Takes as input the Atlas labels path and ROI Number and outputs the ROI name for that atlas
        '''
        atlasDict = {}
        root = ET.parse(atlasLabelsPath).getroot()
        elem = root.find('data')
        for regionRow in elem.getchildren():
            # roiNumber  = int(regionRow.items()[2][1]) + 1 .items() gives the items in arbitary order so indexing changes
            roiNumber = int(regionRow.get(key='index')) + 1
            roiName = regionRow.text
            atlasDict[roiNumber] = roiName

        return atlasDict[roiNum]
     
    def getAtlasRegions(self, coordMni):
        '''
        Takes as input MNI coordinates and returns a tuple (ROI_number, Region_name, Atlas_index_used)
        '''
        roiNumber = None
        roiName = None
        
        
        atlasIndex = 0
        # Enumerates over all the given atlases and stops when the region is found in some atlas. 
        
        global_roiNumber = None 
        global_final_coord = None
        global_final_itr = None
        global_max_prob = 0
        global_max_prob_index = 0
        
        out = []
        for index,atlasPath in enumerate(self.atlasPaths):
            
            if roiNumber == None or self.prob == True:
#                 _atlas = nib.load(atlasPath)
#                 atlas = _atlas.get_data()
#                 if _atlas.header['pixdim'][1] == 2:
                if self.pixdim_list[index] == 2:
                    x,y,z = self.MNI2XYZ2mm(coordMni)
#                 elif _atlas.header['pixdim'][1] == 1:
                elif self.pixdim_list[index] == 1: 
                    x,y,z = self.MNI2XYZ1mm(coordMni)
                else:
                    raise Exception('Unknown Pixel Dimension', _atlas.header['pixdim'][1] )

                
#                 roiNumber = atlas[x,y,z]
                if self.prob == False:
                    roiNumber = self.atlas_list[index][x,y,z]
                else:
                    vec_of_prob = self.atlas_list[index][x,y,z,:]
                    roiNumber = np.argmax(vec_of_prob) + 1 # [1 ... num_roi's]
                    max_prob =  vec_of_prob[roiNumber]
                    if max_prob == 0: # # Coordinate is outside the atlas
                        
                        _roiNumber, _final_coord, _final_itr, _max_prob = self.get_neighbouring_coordinates(x,y,z,self.itr,index, largest= 2)
                        
                        # Getting the Highest probability region
                        if len(_roiNumber) == 0:
                            continue
                            
                        roiNumber=_roiNumber[0]
                        final_coord=_final_coord[0]
                        final_itr=_final_itr[0]
                        max_prob=_max_prob[0]


                if roiNumber != 0:
                    roiName = self.roiName(self.atlasLabelsPaths[index], roiNumber)
                    
                    roiName  = roiName.strip()
                    
                    if self.prob == True:
                    
                        if roiName == 'Right Cerebral White Matter' or roiName == 'Left Cerebral White Matter'\
                        or roiName == 'Left Cerebral Cortex' or roiName == 'Right Cerebral Cortex':
                            # Look for second largest in the same atlas
                            if len(_roiNumber) > 1: # If second highest prob region exists 
                                # Getting the second Highest probability region
                                roiNumber=_roiNumber[1]
                                final_coord=_final_coord[1]
                                final_itr=_final_itr[1]
                                max_prob=_max_prob[1]
                                
                                
                            else:
                                roiNumber = None
                                atlasIndex = atlasIndex + 1
                                continue
                        
#                         if global_max_prob < max_prob:
#                             global_max_prob_index = atlasIndex
#                             global_max_prob = max_prob

                        out.append([roiNumber, roiName ,final_coord ,final_itr, max_prob, index])

                                
                    else:
                        if roiName == 'Right Cerebral White Matter' or roiName == 'Left Cerebral White Matter'\
                        or roiName == 'Left Cerebral Cortex' or roiName == 'Right Cerebral Cortex':
                            roiNumber = None
                            atlasIndex = atlasIndex + 1
                            continue
                        
                        
                            

                else:
                    roiNumber = None
                    atlasIndex = atlasIndex + 1
                
        
        final_output_idx = 0
        final_max_prob = 0
        for idx,output in enumerate(out):
            if final_max_prob < output[4]:
                final_output_idx = idx
                final_max_prob = output[4]
                
        roiNumber, roiName, atlasIndex = output[0], output[1], output[5] 
                
                    

        if roiNumber == None:
            roiNumber, roiName, atlasIndex = 0, None, None
            
        return int(roiNumber), roiName, atlasIndex
    
    
    def get_neighbouring_coordinates(self,x,y,z, itr, atlas_index, largest=1):
        final_coord = [x,y,z]
        old_dist = float('Inf')
        final_itr = [0,0,0]
        final_roi = 0
        
        
        final_roi_list = []
        final_coord_list = []
        final_itr_list = []
        final_max_prob_list = []
        
        
        roi_list = []
        coord_list = []
        itr_list = []
        max_prob_list = []
        
        
        for xi in itr:
            for yi in itr:
                for zi in itr:
                    roi_list = []
                    coord_list = []
                    itr_list = []
                    max_prob_list = []
                    vec_of_prob = np.array(self.atlas_list[atlas_index][x-xi,y-yi,z-zi,:])
                    for counter in range(largest):
                        
                        roiNumber = np.argmax(vec_of_prob) + 1 # [1 ... num_roi's]
                        max_prob =  vec_of_prob[roiNumber - 1]
    #                     print('coord',x-xi,y-yi,z-zi)
    #                     print('MAx_prob',max_prob)
                        if max_prob != 0: # the max roi lies inside the atlas
                            dist = abs(xi) +  abs(yi)  + abs(zi)
                            if dist <= old_dist: #or final_itr == [0,0,0]
                                print(old_dist, dist)
                                old_dist = dist
                                coord_list.append([x-xi, y-yi, z-zi])
                                final_itr = [xi,yi,zi]
                                print(final_itr)
                                itr_list.append([xi,yi,zi])
                                roi_list.append(roiNumber)
                                max_prob_list.append(max_prob)
                        
                        vec_of_prob[roiNumber - 1] = 0
                        
                    if len(roi_list) != 0:
                        final_roi_list = roi_list 
                        final_coord_list = coord_list 
                        final_itr_list = itr_list 
                        final_max_prob_list = max_prob_list 
                        
        return final_roi_list, final_coord_list, final_itr_list, final_max_prob_list


In [32]:
# a = np.array([1,2,3,4,5])
# b = np.array(a)
# b[1] =100
# a,b
# b = np.delete(b,1)
# b

In [52]:
# atlasPaths1  = ['hoAtlas/HarvardOxford-cort-maxprob-thr25-2mm.nii.gz',\
#                'hoAtlas/HarvardOxford-sub-maxprob-thr25-2mm.nii.gz',
#                'cerebellumAtlas/Cerebellum-MNIflirt-maxprob-thr25-1mm.nii.gz']
# atlasLabelsPaths1 = ['hoAtlas/HarvardOxford-Cortical.xml','hoAtlas/HarvardOxford-Subcortical.xml',\
#                     'cerebellumAtlas/Cerebellum_MNIflirt.xml']

# atlasPaths1  = ['hoAtlas/HarvardOxford-cort-maxprob-thr0-1mm.nii.gz',\
#                'hoAtlas/HarvardOxford-sub-maxprob-thr0-1mm.nii.gz',
#                'cerebellumAtlas/Cerebellum-MNIflirt-maxprob-thr0-1mm.nii.gz']
# atlasLabelsPaths1 = ['hoAtlas/HarvardOxford-Cortical.xml','hoAtlas/HarvardOxford-Subcortical.xml',\
#                     'cerebellumAtlas/Cerebellum_MNIflirt.xml']



# atlasPaths1  = ['hoAtlas/HarvardOxford-sub-maxprob-thr0-1mm.nii.gz',\
#                'hoAtlas/HarvardOxford-cort-maxprob-thr0-1mm.nii.gz',
#                'cerebellumAtlas/Cerebellum-MNIflirt-maxprob-thr0-1mm.nii.gz']

atlasPaths1  = ['hoAtlas/HarvardOxford-sub-prob-1mm.nii.gz',\
               'hoAtlas/HarvardOxford-cort-prob-1mm.nii.gz',
               'cerebellumAtlas/Cerebellum-MNIflirt-prob-1mm.nii.gz']


atlasLabelsPaths1 = ['hoAtlas/HarvardOxford-Subcortical.xml','hoAtlas/HarvardOxford-Cortical.xml',\
                    'cerebellumAtlas/Cerebellum_MNIflirt.xml']


del q1
q1 = queryAtlas(atlasPaths1,atlasLabelsPaths1,True)

Atlas read
checked Pixel dimension
Atlas read
checked Pixel dimension
Atlas read
checked Pixel dimension


In [63]:
# q1.getAtlasRegions([-6,62,-2])
q1.getAtlasRegions([47,-60, 4])

# q1.getAtlasRegions([33, -6, -6])

(13, 'Middle Temporal Gyrus, temporooccipital part', 1)

In [53]:
# q1.itr
q1.getAtlasRegions([47,-60, 4])
# q1.MNI2XYZ1mm( [47,-60, 4])
# q1.MNI2XYZ1mm([-45, 30, 67])
# q1.get_neighbouring_coordinates(135,156,39,q1.itr,0,2)
# q1.get_neighbouring_coordinates(43, 66, 76,q1.itr,2,2)


inf 0
[0, 0, 0]
0 0
[0, 0, 0]
inf 0
[0, 0, 0]
0 0
[0, 0, 0]


(13, 'Middle Temporal Gyrus, temporooccipital part', 1)

In [64]:
# atlasPath2 = ['juelichAtlas/Juelich-maxprob-thr25-1mm.nii.gz']
atlasPath2 = ['juelichAtlas/Juelich-maxprob-thr0-1mm.nii.gz']
atlasLabelsPath2 = ['juelichAtlas/Juelich.xml']
q2 = queryAtlas(atlasPath2,atlasLabelsPath2)

In [65]:
q2.getAtlasRegions([33, -6, -6])

(114, 'WM Uncinate fascicle R', 0)

In [25]:
class addAtlasNamestoCSV:
    def __init__(self,BNAtlasObj,HOAtlasObj,JuliechAtlasObj):
        self.BNAtlasObj = BNAtlasObj
        self.HOAtlasObj = HOAtlasObj
        self.JuliechAtlasObj = JuliechAtlasObj
      
    @staticmethod
    def extract_columns_and_save_CSV(self,csv_path, column_index_include, filename):
        """
        Reads CSV file and saves the selected columns 
        Returns pandas data frame                            
        Can be called as addAtlasNamestoCSV.extract_columns_and_save_CSV() or self.extract_columns_and_save_CSV()
        """
        column_index_include = np.array(column_index_include)                                    
        df = pd.read_csv(csv_path)
        df_extracted = df.iloc[:,column_index_include]
        df_extracted.to_csv(fileName)        
        return df_extracted
       
    
    def addNameCSV(self, csvPath, filename, column_index_include):
        # read CSV file
        df = pd.read_csv(csvPath)
        
        column_index_include = np.array(column_index_include)
        
        dfExtra = df.iloc[:,column_index_include]
        
        dfMatrix = df.as_matrix(['S_No','PaperID','SeedName', 'SeedMNI', 'UnderConnectivityName', 'UnderConnectivityMNI', 'OverConnectivityName',\
             'OverConnectivityMNI'])
        
        
        df_new = pd.DataFrame()
        
        for ix, row in enumerate(tqdm(dfMatrix)):
            s_no, paperID, seedName, seedMNI, underConnectivityName, underConnectedMNI,overConnectivityName, overConnectedMNI = row
            
            underConnectivityNameHO = None
            overConnectivityNameHO = None
            hemisphereSeed=None
            hemisphereUC=None
            hemisphereOC=None
            
            
            #-------Check if MNI is NAN-----
            
            if not pd.isna(seedMNI):

                seedMNI = seedMNI.strip('\n')
                seedMNIint = seedMNI.split(' ')
                seedMNIint = [x for x in seedMNIint if x != '']  
                
                try:
                    seedMNIint = list(map(int, seedMNIint))
                except ValueError as v:
                    print(v)
                    print('error at S.No %s'% s_no)
                
            
                assert (len(seedMNIint) == 3), "Seed MNI Coordinates Error at S.No %s" % s_no
                
                if seedMNIint[0] < 0:
                    hemisphereSeed = 'L'
                elif seedMNIint[0] > 0:
                    hemisphereSeed = 'R'
                else:
                    hemisphereSeed = 'C'


                seed_x = seedMNIint[0]
                seed_y = seedMNIint[1]
                seed_z = seedMNIint[2]


                _,seedNameHO,_ = self.HOAtlasObj.getAtlasRegions(seedMNIint)
                _,seedNameJuliech,_ = self.JuliechAtlasObj.getAtlasRegions(seedMNIint)

                _,seedLobe, seedGyrus, seedNameBN = self.BNAtlasObj.getAtlasRegions(seedMNIint)
            
            else:
                seedNameHO = np.nan
                seedNameJuliech = np.nan
                seedLobe = np.nan
                seedGyrus = np.nan
                seedNameBN = np.nan
                hemisphereSeed = np.nan
                seed_x = np.nan
                seed_y = np.nan
                seed_z = np.nan
                


            if not pd.isna(underConnectedMNI):
                underConnectedMNI = underConnectedMNI.strip('\n')
                underConnectedMNIint = underConnectedMNI.split(' ')
                underConnectedMNIint = [x for x in underConnectedMNIint if x != '']

                try:
                    underConnectedMNIint = list(map(int, underConnectedMNIint))
                except ValueError as v:
                    print(v)
                    print('error at S.No %s'% s_no)
                    
                assert (len(underConnectedMNIint) == 3), "Underconn. MNI Coordinates Error at S.No %s" % s_no
                
                if underConnectedMNIint[0] < 0:
                    hemisphereUC = 'L'
                elif underConnectedMNIint[0] > 0:
                    hemisphereUC = 'R'
                else:
                    hemisphereUC = 'C'



                connectivity_x = underConnectedMNIint[0]
                connectivity_y = underConnectedMNIint[1]
                connectivity_z = underConnectedMNIint[2]

                _,connectivityNameHO,_ = self.HOAtlasObj.getAtlasRegions(underConnectedMNIint)
                _,connectivityNameJuliech,_ = self.JuliechAtlasObj.getAtlasRegions(underConnectedMNIint)

                _,connectivityLobe, connectivityGyrus, connectivityNameBN = self.BNAtlasObj.getAtlasRegions(underConnectedMNIint)


                _df = pd.DataFrame({'S_No': [s_no],
                                    'PaperID':[paperID],
                                    'SeedHemisphere':[hemisphereSeed],
                                     'SeedLobe':[seedLobe],
                                     'SeedGyrus':[seedGyrus],
                                     'SeedNameBN':[seedNameBN],
                                     'SeedNameHO':[seedNameHO],
                                     'SeedNameJuliech':[seedNameJuliech],
                                     'SeedName':[seedName],
                                     'Seed_X':[seed_x],
                                     'Seed_Y':[seed_y],
                                     'Seed_Z':[seed_z],
                                     'ConnectivityHemisphere':[hemisphereUC],
                                     'ConnectivityLobe':[connectivityLobe],
                                     'ConnectivityGyrus':[connectivityGyrus],
                                     'ConnectivityNameBN':[connectivityNameBN],
                                     'ConnectivityNameHO':[connectivityNameHO],
                                     'ConnectivityNameJuliech':[connectivityNameJuliech],
                                     'ConnectivityName':[underConnectivityName],
                                     'Connectivity_X':[connectivity_x],
                                     'Connectivity_Y':[connectivity_y],
                                     'connectivity_Z':[connectivity_z],
                                     'Under(-1)/Over(1)Connectivity':[-1],

              })


                dat1 = dfExtra[ix:ix+1]
                dat2 = _df

                dat1 = dat1.reset_index(drop=True)
                dat2 = dat2.reset_index(drop=True)

                temp = pd.concat([dat1,dat2],axis=1)
                df_new = df_new.append(temp)


            if not pd.isna(overConnectedMNI):
                overConnectedMNI = overConnectedMNI.strip('\n')
                overConnectedMNIint = overConnectedMNI.split(' ')
                overConnectedMNIint = [x for x in overConnectedMNIint if x != '']
                
                try:
                    overConnectedMNIint = list(map(int, overConnectedMNIint))
                except ValueError as v:
                    print(v)
                    print('error at S.No %s'% s_no)
                
                assert (len(overConnectedMNIint) == 3), "Overconn. MNI Coordinates Error at S.No %s" % s_no
                
                if overConnectedMNIint[0] < 0:
                    hemisphereOC = 'L'
                elif overConnectedMNIint[0] > 0:
                    hemisphereOC = 'R'
                else:
                    hemisphereOC = 'C'


                connectivity_x = overConnectedMNIint[0]
                connectivity_y = overConnectedMNIint[1]
                connectivity_z = overConnectedMNIint[2]

                _,connectivityNameHO,_ = self.HOAtlasObj.getAtlasRegions(overConnectedMNIint)
                _,connectivityNameJuliech,_ = self.JuliechAtlasObj.getAtlasRegions(overConnectedMNIint)

                _,connectivityLobe, connectivityGyrus, connectivityNameBN = self.BNAtlasObj.getAtlasRegions(overConnectedMNIint)


                _df = pd.DataFrame({'S_No': [s_no],
                                    'PaperID':[paperID],
                                    'SeedHemisphere':[hemisphereSeed],
                                     'SeedLobe':[seedLobe],
                                     'SeedGyrus':[seedGyrus],
                                     'SeedNameBN':[seedNameBN],
                                     'SeedNameHO':[seedNameHO],
                                     'SeedNameJuliech':[seedNameJuliech],
                                     'SeedName':[seedName],
                                     'Seed_X':[seed_x],
                                     'Seed_Y':[seed_y],
                                     'Seed_Z':[seed_z],
                                     'ConnectivityHemisphere':[hemisphereOC],
                                     'ConnectivityLobe':[connectivityLobe],
                                     'ConnectivityGyrus':[connectivityGyrus],
                                     'ConnectivityNameBN':[connectivityNameBN],
                                     'ConnectivityNameHO':[connectivityNameHO],
                                     'ConnectivityNameJuliech':[connectivityNameJuliech],
                                     'ConnectivityName':[overConnectivityName],
                                     'Connectivity_X':[connectivity_x],
                                     'Connectivity_Y':[connectivity_y],
                                     'connectivity_Z':[connectivity_z],
                                     'Under(-1)/Over(1)Connectivity':[1],

              })






                dat1 = dfExtra[ix:ix+1]
                dat2 = _df

                dat1 = dat1.reset_index(drop=True)
                dat2 = dat2.reset_index(drop=True)

                temp = pd.concat([dat1,dat2],axis=1)
                df_new = df_new.append(temp)



       
        cols=['S_No','PaperID','SeedHemisphere','SeedLobe','SeedGyrus', 'SeedNameBN',\
                                       'SeedNameHO','SeedNameJuliech','SeedName',\
                                       'Seed_X','Seed_Y','Seed_Z', 'ConnectivityHemisphere','ConnectivityLobe',
                                       'ConnectivityGyrus','ConnectivityNameBN',\
                                       'ConnectivityNameHO','ConnectivityNameJuliech','ConnectivityName','Connectivity_X',\
                                       'Connectivity_Y','connectivity_Z', 'Under(-1)/Over(1)Connectivity']
        
        
      
        df_new = df_new.loc[:,dfExtra.columns.append(pd.Index(cols))]
#         fileName = 'connectivityResults2.csv'1

        print('Saving the CSV file of links at %s'% filename)
        df_new.to_csv(filename)

        return df_new 

    @staticmethod
    def remove_duplicate_rows(columns_index, in_file, out_file):
        # TODO:
        # Find the S.No that has duplicate entries
        # Delete that Row
        
        # read CSV file
        csvPath = in_file
        df = pd.read_csv(csvPath)
        columns_check = list(df.columns[column_index])

        df_extracted = df.drop_duplicates(subset=columns_check,keep='first')
        df_extracted.to_csv(out_file)
        return df_extracted
 
    @staticmethod
    def find_consistent_conflicting_links(df, columns_match_index, connectivity_column_index, s_no_column_index,\
                                          paper_id_column_index,merge_hemispheres):    
        conflicts = []
        consistent = []

        df_conflicts_details = pd.DataFrame()
        df_consistent_details = pd.DataFrame()

        if merge_hemispheres:
            _columns_match_index = np.array(columns_match_index)[[0,1,3]]
            print('Hemispheres merged while checking consistency')
        else:
            _columns_match_index = columns_match_index

        for ix1, (Index, row1) in  tqdm(enumerate(df.iterrows())):
            for ix2, row2 in df[ix1+1:].iterrows():
#                 print(row1[1], row2[1]) # printing S_no pairs
                # if all the columns match
                if (row1[_columns_match_index] == row2[_columns_match_index]).sum() == len(_columns_match_index):  
                    if (row1[connectivity_column_index] !=  row2[connectivity_column_index]).sum() == len(connectivity_column_index):
                        # Conflict
                        conflicts.append([(row1[s_no_column_index].item(), row2[s_no_column_index].item()),\
                                          (row1[paper_id_column_index].item(), row2[paper_id_column_index].item())])

                        
                        _df = pd.DataFrame({'S_No_link1': [row1[s_no_column_index].item()],
                                            'PaperID_link1':[row1[paper_id_column_index].item()],
                                            'SeedHemisphere_link1':[row1[columns_match_index[0]]],
                                             'SeedNameHO_link1':[row1[columns_match_index[1]]],
                                             'ConnectivityHemisphere_link1':[row1[columns_match_index[2]]],
                                             'ConnectivityNameHO_link1':[row1[columns_match_index[3]]],
                                             'Under(-1)/Over(1)Connectivity_link1':[row1[connectivity_column_index].item()],

                                            'S_No_link2': [row2[s_no_column_index].item()],
                                            'PaperID_link2':[row2[paper_id_column_index].item()],
                                            'SeedHemisphere_link2':[row2[columns_match_index[0]]],
                                             'SeedNameHO_link2':[row2[columns_match_index[1]]],
                                             'ConnectivityHemisphere_link2':[row2[columns_match_index[2]]],
                                             'ConnectivityNameHO_link2':[row2[columns_match_index[3]]],
                                             'Under(-1)/Over(1)Connectivity_link2':[row2[connectivity_column_index].item()]

                        })

                        df_conflicts_details = df_conflicts_details.append(_df)
                    else:
                        # Consistent
                        consistent.append([(row1[s_no_column_index].item(), row2[s_no_column_index].item()),\
                                          (row1[paper_id_column_index].item(), row2[paper_id_column_index].item())])


                        _df = pd.DataFrame({'S_No_link1': [row1[s_no_column_index].item()],
                                            'PaperID_link1':[row1[paper_id_column_index].item()],
                                            'SeedHemisphere_link1':[row1[columns_match_index[0]]],
                                             'SeedNameHO_link1':[row1[columns_match_index[1]]],
                                             'ConnectivityHemisphere_link1':[row1[columns_match_index[2]]],
                                             'ConnectivityNameHO_link1':[row1[columns_match_index[3]]],
                                             'Under(-1)/Over(1)Connectivity_link1':[row1[connectivity_column_index].item()],

                                            'S_No_link2': [row2[s_no_column_index].item()],
                                            'PaperID_link2':[row2[paper_id_column_index].item()],
                                            'SeedHemisphere_link2':[row2[columns_match_index[0]]],
                                             'SeedNameHO_link2':[row2[columns_match_index[1]]],
                                             'ConnectivityHemisphere_link2':[row2[columns_match_index[2]]],
                                             'ConnectivityNameHO_link2':[row2[columns_match_index[3]]],
                                             'Under(-1)/Over(1)Connectivity_link2':[row2[connectivity_column_index].item()]

                        })

                        df_consistent_details = df_consistent_details.append(_df)
                        
        return df_conflicts_details, df_consistent_details
                        



In [19]:
csvPath = 'csv_input/als.csv'
df = pd.read_csv(csvPath)

# column_index_include = np.array(column_index_include)
# dfExtra = df.iloc[:,column_index_include]

# dfMatrix = df.as_matrix(['S_No','PaperID','SeedName', 'SeedMNI', 'UnderConnectivityName', 'UnderConnectivityMNI', 'OverConnectivityName',\
#      'OverConnectivityMNI'])


# df.columns
ind = np.arange(len(df.columns))
for entry in zip(ind,df.columns):
    print(entry)

(0, 'S_No')
(1, 'PaperID')
(2, 'Title')
(3, 'TR ')
(4, 'Volumes')
(5, 'ScanTime(Min.Sec)')
(6, 'EyeStatus')
(7, 'MFStrength')
(8, 'NumHealthy(M)')
(9, 'NumHealthy(F)')
(10, 'NumASD(M)')
(11, 'NumASD(F)')
(12, 'NumAutistic')
(13, 'NumHighFunctioning')
(14, 'LanguageImpaired')
(15, "NumAspergsr's")
(16, 'NumPDD-NOS')
(17, 'AgeRangeHealthyMean')
(18, 'AgeRangeHealthyStd')
(19, 'AgeRangeASDMean')
(20, 'AgeRangeASDStd')
(21, 'AgeRangeAutistic')
(22, "AgeRangeAspergsr's")
(23, 'AgeRangePDD-NOS')
(24, 'FIQMean_ASD')
(25, 'FIQStd_ASD')
(26, 'FIQMean_TD')
(27, 'FIQStd_TD')
(28, 'BandpassRangeHighpass(Hz)')
(29, 'BandpassRangeLowpass(Hz)')
(30, 'Smoothing(fwhm)mm')
(31, 'GSR')
(32, 'CSF')
(33, 'WM')
(34, 'Motion Params')
(35, 'Age')
(36, 'Scrubbing')
(37, 'GCOR')
(38, 'aCOMPCor')
(39, 'Cardiac and respiratory signals regression')
(40, 'Despiking')
(41, 'SeedName')
(42, 'SeedMNI')
(43, 'UnderConnectivityName')
(44, 'UnderConnectivityMNI')
(45, 'OverConnectivityName')
(46, 'OverConnectivityMNI')
(

In [26]:
atlas_path = 'brainnetomeAtlas/BNA-maxprob-thr0-1mm.nii.gz'
atlasRegionsDescrpPath = 'brainnetomeAtlas/BNA_subregions_machineReadable.xlsx'
BNAtlasObj = queryBrainnetomeROI(atlas_path, atlasRegionsDescrpPath)


# atlasPaths1  = ['hoAtlas/HarvardOxford-cort-maxprob-thr25-2mm.nii.gz',\
#                'hoAtlas/HarvardOxford-sub-maxprob-thr25-2mm.nii.gz',
#                'cerebellumAtlas/Cerebellum-MNIflirt-maxprob-thr25-1mm.nii.gz']
# atlasLabelsPaths1 = ['hoAtlas/HarvardOxford-Cortical.xml','hoAtlas/HarvardOxford-Subcortical.xml',\
#                     'cerebellumAtlas/Cerebellum_MNIflirt.xml']

atlasPaths1  = ['hoAtlas/HarvardOxford-sub-maxprob-thr0-1mm.nii.gz',\
               'hoAtlas/HarvardOxford-cort-maxprob-thr0-1mm.nii.gz',
               'cerebellumAtlas/Cerebellum-MNIflirt-maxprob-thr0-1mm.nii.gz']
atlasLabelsPaths1 = ['hoAtlas/HarvardOxford-Subcortical.xml','hoAtlas/HarvardOxford-Cortical.xml',\
                    'cerebellumAtlas/Cerebellum_MNIflirt.xml']


HOAtlasObj = queryAtlas(atlasPaths1,atlasLabelsPaths1)


atlasPath2 = ['juelichAtlas/Juelich-maxprob-thr25-1mm.nii.gz']
atlasLabelsPath2 = ['juelichAtlas/Juelich.xml']

JuliechAtlasObj = queryAtlas(atlasPath2,atlasLabelsPath2)


csvPath = 'csv_input/als.csv'
q = addAtlasNamestoCSV(BNAtlasObj, HOAtlasObj, JuliechAtlasObj)

# columns_index_include = [0,1,28,29,30,31]

# columns_index_include = [0,1]
# columns_index_include.extend(list(np.arange(3,41)))

columns_index_include = list(np.arange(3,41))

filename = 'csv_output/finalLinks_all_columns.csv'
df = q.addNameCSV(csvPath, filename, columns_index_include)
# df = q.addNameCSV(csvPath, filename)




100%|██████████| 759/759 [15:03<00:00,  1.19s/it]

Saving the CSV file of links at csv_output/finalLinks_all_columns.csv


In [27]:
len(df)

897

In [39]:
def show_columns(df):
    
    if isinstance(df,str):
        df = pd.read_csv(df)
    
    ind = np.arange(len(df.columns))

    for entry in zip(ind,df.columns):
        print(entry)

In [41]:
show_columns(df)

(0, 'Unnamed: 0')
(1, 'TR ')
(2, 'Volumes')
(3, 'ScanTime(Min.Sec)')
(4, 'EyeStatus')
(5, 'MFStrength')
(6, 'NumHealthy(M)')
(7, 'NumHealthy(F)')
(8, 'NumASD(M)')
(9, 'NumASD(F)')
(10, 'NumAutistic')
(11, 'NumHighFunctioning')
(12, 'LanguageImpaired')
(13, "NumAspergsr's")
(14, 'NumPDD-NOS')
(15, 'AgeRangeHealthyMean')
(16, 'AgeRangeHealthyStd')
(17, 'AgeRangeASDMean')
(18, 'AgeRangeASDStd')
(19, 'AgeRangeAutistic')
(20, "AgeRangeAspergsr's")
(21, 'AgeRangePDD-NOS')
(22, 'FIQMean_ASD')
(23, 'FIQStd_ASD')
(24, 'FIQMean_TD')
(25, 'FIQStd_TD')
(26, 'BandpassRangeHighpass(Hz)')
(27, 'BandpassRangeLowpass(Hz)')
(28, 'Smoothing(fwhm)mm')
(29, 'GSR')
(30, 'CSF')
(31, 'WM')
(32, 'Motion Params')
(33, 'Age')
(34, 'Scrubbing')
(35, 'GCOR')
(36, 'aCOMPCor')
(37, 'Cardiac and respiratory signals regression')
(38, 'Despiking')
(39, 'S_No')
(40, 'PaperID')
(41, 'SeedHemisphere')
(42, 'SeedLobe')
(43, 'SeedGyrus')
(44, 'SeedNameBN')
(45, 'SeedNameHO')
(46, 'SeedNameJuliech')
(47, 'SeedName')
(48, 'Se

# Remove Duplicates

In [32]:
# Remove Duplicates: For each paper ID independently, remove the link that has same hemisphere HO region
# as source and target and that has same connectivity value  
in_file = 'csv_output/finalLinks_all_columns.csv'
out_file = 'csv_output/finalLinks_duplicates_removed_all_columns.csv'
# column_index = [4,13,17,23,27,33]

column_index = [40,41,45,51,55,61]
df_extracted = addAtlasNamestoCSV.remove_duplicate_rows(column_index,in_file,out_file)

In [34]:
df_extracted

Unnamed: 0    TR  Volumes ScanTime(Min.Sec) EyeStatus MFStrength  \
0             0   2000     NaN               5.4      Open          3   
1             0   2000     NaN               5.4      Open          3   
2             0   2000     NaN               5.4      Open          3   
3             0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
4             0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
5             0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
6             0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
7             0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
8             0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
9             0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
10            0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
11            0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
12            0   2080     220               7.2    Closed          3   
13            0   2080     220               7.2    Closed          3   
14            0   2080     220               7.2    Closed          3   
15            0   2080     220               7.2    Closed          3   
16            0   2080     220               7.2    Closed          3   
17            0   2080     220               7.2    Closed          3   
19            0   2080     220               7.2    Closed          3   
20            0   2080     220               7.2    Closed          3   
21            0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
22            0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
23            0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
24            0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
25            0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
26            0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
27            0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
28            0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
29            0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
30            0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
..          ...    ...     ...               ...       ...        ...   
864           0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
867           0  ABIDE   ABIDE             ABIDE     ABIDE      ABIDE   
869           0   2000     185              6.16         -          3   
870           0   2000     185              6.16         -          3   
871           0   2000     185              6.16         -          3   
872           0   2000     185              6.16         -          3   
873           0   2000     185              6.16         -          3   
874           0   2000     185              6.16         -          3   
875           0   2000     185              6.16         -          3   
876           0   2000     185              6.16         -          3   
877           0   2000     185              6.16         -          3   
878           0   2000     185              6.16         -          3   
879           0   2000     185              6.16         -          3   
880           0   2000     185              6.16         -          3   
881           0   2000     185              6.16         -          3   
882           0   2000     185              6.16         -          3   
883           0   2000     185              6.16         -          3   
884           0   2000     185              6.16         -          3   
885           0   2000     185              6.16         -          3   
886           0   2000     185              6.16         -          3   
887           0   2000     185              6.16         -          3   
888           0   2000     185              6.16         -          3   
889           0   2000     185              6.16         -     

In [33]:
len(df_extracted)

721

In [42]:
show_columns(df_extracted)

(0, 'Unnamed: 0')
(1, 'TR ')
(2, 'Volumes')
(3, 'ScanTime(Min.Sec)')
(4, 'EyeStatus')
(5, 'MFStrength')
(6, 'NumHealthy(M)')
(7, 'NumHealthy(F)')
(8, 'NumASD(M)')
(9, 'NumASD(F)')
(10, 'NumAutistic')
(11, 'NumHighFunctioning')
(12, 'LanguageImpaired')
(13, "NumAspergsr's")
(14, 'NumPDD-NOS')
(15, 'AgeRangeHealthyMean')
(16, 'AgeRangeHealthyStd')
(17, 'AgeRangeASDMean')
(18, 'AgeRangeASDStd')
(19, 'AgeRangeAutistic')
(20, "AgeRangeAspergsr's")
(21, 'AgeRangePDD-NOS')
(22, 'FIQMean_ASD')
(23, 'FIQStd_ASD')
(24, 'FIQMean_TD')
(25, 'FIQStd_TD')
(26, 'BandpassRangeHighpass(Hz)')
(27, 'BandpassRangeLowpass(Hz)')
(28, 'Smoothing(fwhm)mm')
(29, 'GSR')
(30, 'CSF')
(31, 'WM')
(32, 'Motion Params')
(33, 'Age')
(34, 'Scrubbing')
(35, 'GCOR')
(36, 'aCOMPCor')
(37, 'Cardiac and respiratory signals regression')
(38, 'Despiking')
(39, 'S_No')
(40, 'PaperID')
(41, 'SeedHemisphere')
(42, 'SeedLobe')
(43, 'SeedGyrus')
(44, 'SeedNameBN')
(45, 'SeedNameHO')
(46, 'SeedNameJuliech')
(47, 'SeedName')
(48, 'Se

# Consistent and conflicting links

In [43]:
# Match the rows having same hemisphere and same HO region


# columns_match_index = [13, 17, 23, 27]

# connectivity_column_index = [33]
# s_no_column_index = [1]
# paper_id_column_index = [3]

columns_match_index = [41,45,51,55]

connectivity_column_index = [61]
s_no_column_index = [39]
paper_id_column_index = [40]


df_conflicts_details, df_consistent_details = addAtlasNamestoCSV.find_consistent_conflicting_links(df_extracted, columns_match_index, connectivity_column_index,\
s_no_column_index, paper_id_column_index, merge_hemispheres = False)

721it [02:01,  5.94it/s]


In [44]:
len(df_consistent_details),len(df_conflicts_details)

(55, 48)

In [66]:
df_consistent_details

ConnectivityHemisphere_link1 ConnectivityHemisphere_link2  \
0                             L                            L   
0                             L                            L   
0                             L                            L   
0                             L                            R   
0                             L                            L   
0                             L                            L   
0                             L                            R   
0                             L                            L   
0                             L                            R   
0                             R                            L   
0                             R                            L   
0                             R                            R   
0                             R                            L   
0                             R                            L   
0                             R                            R   
0                             L                            R   
0                             R                            L   
0                             R                            L   
0                             L                            R   
0                             R                            L   
0                             R                            L   
0                             R                            R   
0                             L                            L   
0                             R                            R   
0                             L                            R   
0                             L                            R   
0                             L                            R   
0                             L                            R   
0                             L                            R   
0                             L                            R   
..                          ...                          ...   
0                             R                            R   
0                             R                            L   
0                             R                            R   
0                             R                            R   
0                             R                            L   
0                             L                            R   
0                             L                            L   
0                             R                            L   
0                             R                            L   
0                             L                            R   
0                             L                            L   
0                             R                            L   
0                             L                            R   
0                             L                            L   
0                             R                            L   
0                             L                            R   
0                             L                            R   
0                             R                            R   
0                             L                            R   
0                             L                            L   
0                             R                            L   
0                             L                            R   
0                             R                            L   
0                             R                            L   
0                             R                            L   
0                             R                            L   
0                             R                            L   
0                             L                            R   
0                             L                            R   
0                             R                            L   

                       Connectivit

In [44]:
df_extracted.iloc[1:4,[23,27]]

ConnectivityHemisphere                   ConnectivityNameHO
1                      L                         Frontal Pole
2                      L  Cingulate Gyrus, posterior division
3                      L                     Planum Temporale

In [ ]:
# Find Conflicting Links
# Same 'SeedNameHO', 'ConnectivityNameHO'
# But different 'Under(-1)/Over(1)Connectivity'
'''
First get all PaperIds.
Select one Row
Loop over all paper IDs/ Rows 
    Find duplicates on columns = ['SeedNameHO', 'ConnectivityNameHO']
    If duplicate is found check the Conenctivity
    If Conflict then report the S.No pair and their corresponding PaperIDs
    [(S_no_source, S_no_target),(paperID_source, paperID_target)]

'''
df.columns['Paper']


# DUMP

In [ ]:
atlasLabelsPath = 'hoAtlas/HarvardOxford-Cortical.xml'
root = ET.parse(atlasLabelsPath).getroot()
elem = root.find('data')

In [ ]:
q = root.getchildren()[1]

In [ ]:
k = q.getchildren()[0]

In [ ]:
k.text

In [ ]:
atlasLabelsPath = 'hoAtlas/HarvardOxford-Cortical.xml'

In [ ]:
elem.getchildren()[0].items()

In [ ]:
r = elem.getchildren()[0]

In [ ]:
r.get(key='x')

In [ ]:
csvPath = 'Literature_Survey_ResultsSheet41.csv'
df = pd.read_csv(csvPath)

In [ ]:
df.columns

In [ ]:
columns_index_include = [0,1,2,3,5,6]
df.columns[columns_index_include]

In [ ]:
df.iloc[:,:29]

In [ ]:
# Selecting individual rows or columns
row = np.array([1,2,4])
col = np.array([1,2,4])
df.iloc[row,col]

In [ ]:
np.arange(4)

In [ ]:
csvPath = 'csv_output/finalLinks1.csv'
column_index = [4,13,17,23,27]
df = pd.read_csv(csvPath)
columns_check = list(df.columns[column_index])

df_extracted = df.drop_duplicates(subset=columns_check,keep='first')
# df_extracted.to_csv(filename)

In [ ]:
len(df), len(df_extracted), columns_check

In [ ]:
df_extracted

In [ ]:
list(df.columns),df.columns[13]

In [ ]:
(df_extracted.iloc[0,[13,14]] == df_extracted.iloc[1,[13,14]]).sum()

In [ ]:
df_extracted.iloc[4,[13,14]]

In [ ]:
pid_column = 3
pd.unique(df[df.columns[pid_column]])

In [ ]:
itr = pd.unique(df[df.columns[pid_column]])
for pid in itr:
    

### Find Inconsistencies

In [130]:
for ix1, row1 in  enumerate(df[0:3].iterrows()):
    for ix2, row2 in enumerate(df[ix1+1:].iterrows()):
        print(row1[1], row2[1]) # printing S_no pairs

Unnamed: 0                                                         0
S_No                                                               1
S_No.1                                                             1
PaperID                                                            1
PaperID.1                                                          1
BandpassRangeHighpass(Hz)                                       0.01
BandpassRangeLowpass(Hz)                                         0.1
Smoothing(fwhm)mm                                                  6
GSR                                                              NaN
S_No.2                                                             1
S_No.3                                                             1
PaperID.2                                                          1
PaperID.3                                                          1
SeedHemisphere                                                     L
SeedLobe                          

Name: 83, dtype: object
Unnamed: 0                                                         0
S_No                                                               1
S_No.1                                                             1
PaperID                                                            1
PaperID.1                                                          1
BandpassRangeHighpass(Hz)                                       0.01
BandpassRangeLowpass(Hz)                                         0.1
Smoothing(fwhm)mm                                                  6
GSR                                                              NaN
S_No.2                                                             1
S_No.3                                                             1
PaperID.2                                                          1
PaperID.3                                                          1
SeedHemisphere                                                     L
SeedLobe  

Name: 0, dtype: object Unnamed: 0                                                                       0
S_No                                                                           193
S_No.1                                                                         193
PaperID                                                                         16
PaperID.1                                                                       16
BandpassRangeHighpass(Hz)                                                      NaN
BandpassRangeLowpass(Hz)                                                       NaN
Smoothing(fwhm)mm                                                              NaN
GSR                                                                            NaN
S_No.2                                                                         193
S_No.3                                                                         193
PaperID.2                                                       

Unnamed: 0                                                         0
S_No                                                               1
S_No.1                                                             1
PaperID                                                            1
PaperID.1                                                          1
BandpassRangeHighpass(Hz)                                       0.01
BandpassRangeLowpass(Hz)                                         0.1
Smoothing(fwhm)mm                                                  6
GSR                                                              NaN
S_No.2                                                             1
S_No.3                                                             1
PaperID.2                                                          1
PaperID.3                                                          1
SeedHemisphere                                                     L
SeedLobe                          

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [126]:
len(df_extracted)

721

In [19]:
df = df_extracted

In [20]:
columns_match_index = [13, 17, 23, 27]
connectivity_column_index = [33]
s_no_column_index = [1]
paper_id_column_index = [3]

conflicts = []
consistent = []

df_conflicts_details = pd.DataFrame()
df_consistent_details = pd.DataFrame()



for ix1, (Index, row1) in  enumerate(df.iterrows()):
    for ix2, row2 in df[ix1+1:].iterrows():
        print(row1[1], row2[1]) # printing S_no pairs
        # if all the columns match
        if (row1[columns_match_index] == row2[columns_match_index]).sum() == len(columns_match_index):  
            if (row1[connectivity_column_index] !=  row2[connectivity_column_index]).sum() == len(connectivity_column_index):
                # Conflict
                conflicts.append([(row1[s_no_column_index].item(), row2[s_no_column_index].item()),\
                                  (row1[paper_id_column_index].item(), row2[paper_id_column_index].item())])

                
                _df = pd.DataFrame({'S_No_link1': [row1[s_no_column_index].item()],
                                    'PaperID_link1':[row1[paper_id_column_index].item()],
                                    'SeedHemisphere_link1':[row1[columns_match_index[0]]],
                                     'SeedNameHO_link1':[row1[columns_match_index[1]]],
                                     'ConnectivityHemisphere_link1':[row1[columns_match_index[2]]],
                                     'ConnectivityNameHO_link1':[row1[columns_match_index[3]]],
                                     'Under(-1)/Over(1)Connectivity_link1':[row1[connectivity_column_index].item()],
                                     
                                    'S_No_link2': [row2[s_no_column_index].item()],
                                    'PaperID_link2':[row2[paper_id_column_index].item()],
                                    'SeedHemisphere_link2':[row2[columns_match_index[0]]],
                                     'SeedNameHO_link2':[row2[columns_match_index[1]]],
                                     'ConnectivityHemisphere_link2':[row2[columns_match_index[2]]],
                                     'ConnectivityNameHO_link2':[row2[columns_match_index[3]]],
                                     'Under(-1)/Over(1)Connectivity_link2':[row2[connectivity_column_index].item()]
                                     
                })

                df_conflicts_details = df_conflicts_details.append(_df)
            else:
                # Consistent
                consistent.append([(row1[s_no_column_index].item(), row2[s_no_column_index].item()),\
                                  (row1[paper_id_column_index].item(), row2[paper_id_column_index].item())])

                
                _df = pd.DataFrame({'S_No_link1': [row1[s_no_column_index].item()],
                                    'PaperID_link1':[row1[paper_id_column_index].item()],
                                    'SeedHemisphere_link1':[row1[columns_match_index[0]]],
                                     'SeedNameHO_link1':[row1[columns_match_index[1]]],
                                     'ConnectivityHemisphere_link1':[row1[columns_match_index[2]]],
                                     'ConnectivityNameHO_link1':[row1[columns_match_index[3]]],
                                     'Under(-1)/Over(1)Connectivity_link1':[row1[connectivity_column_index].item()],
                                     
                                    'S_No_link2': [row2[s_no_column_index].item()],
                                    'PaperID_link2':[row2[paper_id_column_index].item()],
                                    'SeedHemisphere_link2':[row2[columns_match_index[0]]],
                                     'SeedNameHO_link2':[row2[columns_match_index[1]]],
                                     'ConnectivityHemisphere_link2':[row2[columns_match_index[2]]],
                                     'ConnectivityNameHO_link2':[row2[columns_match_index[3]]],
                                     'Under(-1)/Over(1)Connectivity_link2':[row2[connectivity_column_index].item()]
                                     
                })

                df_consistent_details = df_consistent_details.append(_df)

        
 # Added hemisphere for check as well coz regions like PCC in HO Atlas is one single ROI and 
 # is not differentiated for Left and Right hemispheres.   
    

1 2
1 3
1 4
1 5
1 6
1 7
1 8
1 9
1 10
1 11
1 12
1 13
1 13
1 14
1 14
1 15
1 15
1 17
1 18
1 19
1 20
1 21
1 22
1 23
1 24
1 25
1 26
1 27
1 28
1 29
1 30
1 31
1 33
1 34
1 38
1 38
1 40
1 41
1 42
1 43
1 44
1 45
1 46
1 47
1 49
1 51
1 52
1 53
1 54
1 55
1 56
1 56
1 57
1 57
1 59
1 60
1 61
1 62
1 63
1 64
1 65
1 66
1 67
1 68
1 69
1 70
1 71
1 72
1 73
1 74
1 75
1 76
1 77
1 78
1 79
1 80
1 81
1 82
1 83
1 84
1 85
1 86
1 87
1 88
1 89
1 90
1 90
1 91
1 91
1 92
1 92
1 93
1 94
1 95
1 96
1 97
1 98
1 99
1 100
1 101
1 102
1 105
1 106
1 108
1 109
1 110
1 111
1 113
1 114
1 115
1 123
1 126
1 127
1 132
1 135
1 139
1 140
1 146
1 148
1 149
1 150
1 151
1 152
1 153
1 154
1 155
1 156
1 157
1 158
1 159
1 159
1 160
1 161
1 162
1 164
1 164
1 165
1 166
1 167
1 168
1 169
1 170
1 171
1 172
1 172
1 173
1 173
1 174
1 174
1 175
1 175
1 176
1 176
1 177
1 178
1 179
1 180
1 181
1 181
1 182
1 182
1 183
1 183
1 184
1 184
1 185
1 185
1 186
1 187
1 188
1 189
1 190
1 191
1 192
1 193
1 194
1 195
1 196
1 197
1 197
1 198
1 198
1 199
1 199
1 

3 217
3 218
3 219
3 220
3 221
3 222
3 223
3 224
3 225
3 226
3 227
3 228
3 229
3 230
3 231
3 232
3 233
3 234
3 235
3 237
3 237
3 238
3 239
3 239
3 240
3 241
3 242
3 244
3 245
3 246
3 247
3 248
3 249
3 251
3 251
3 252
3 253
3 254
3 255
3 256
3 257
3 258
3 260
3 261
3 261
3 262
3 262
3 263
3 264
3 265
3 267
3 269
3 269
3 270
3 270
3 271
3 272
3 273
3 274
3 275
3 276
3 277
3 279
3 280
3 281
3 282
3 283
3 284
3 286
3 288
3 289
3 290
3 291
3 292
3 293
3 294
3 295
3 297
3 298
3 299
3 300
3 301
3 302
3 303
3 304
3 305
3 306
3 307
3 308
3 309
3 310
3 311
3 312
3 320
3 321
3 322
3 323
3 324
3 325
3 326
3 327
3 328
3 328
3 329
3 329
3 330
3 330
3 331
3 331
3 332
3 332
3 333
3 334
3 334
3 335
3 335
3 336
3 336
3 337
3 337
3 338
3 338
3 339
3 340
3 341
3 342
3 343
3 344
3 345
3 346
3 347
3 348
3 349
3 350
3 351
3 352
3 353
3 354
3 355
3 356
3 357
3 358
3 359
3 360
3 361
3 362
3 363
3 364
3 365
3 366
3 367
3 368
3 369
3 370
3 371
3 373
3 374
3 375
3 376
3 377
3 378
3 379
3 380
3 381
3 382
3 383
3 38

5 303
5 304
5 305
5 306
5 307
5 308
5 309
5 310
5 311
5 312
5 320
5 321
5 322
5 323
5 324
5 325
5 326
5 327
5 328
5 328
5 329
5 329
5 330
5 330
5 331
5 331
5 332
5 332
5 333
5 334
5 334
5 335
5 335
5 336
5 336
5 337
5 337
5 338
5 338
5 339
5 340
5 341
5 342
5 343
5 344
5 345
5 346
5 347
5 348
5 349
5 350
5 351
5 352
5 353
5 354
5 355
5 356
5 357
5 358
5 359
5 360
5 361
5 362
5 363
5 364
5 365
5 366
5 367
5 368
5 369
5 370
5 371
5 373
5 374
5 375
5 376
5 377
5 378
5 379
5 380
5 381
5 382
5 383
5 384
5 385
5 387
5 388
5 389
5 390
5 391
5 391
5 392
5 392
5 393
5 393
5 394
5 394
5 395
5 395
5 396
5 397
5 398
5 398
5 399
5 400
5 401
5 401
5 402
5 402
5 403
5 404
5 405
5 405
5 406
5 407
5 407
5 408
5 408
5 409
5 409
5 410
5 410
5 411
5 411
5 412
5 413
5 413
5 414
5 415
5 416
5 417
5 417
5 418
5 419
5 420
5 421
5 423
5 424
5 426
5 427
5 428
5 429
5 430
5 430
5 431
5 431
5 433
5 434
5 434
5 435
5 435
5 436
5 436
5 437
5 439
5 439
5 440
5 441
5 441
5 442
5 443
5 443
5 444
5 444
5 445
5 445
5 44

7 290
7 291
7 292
7 293
7 294
7 295
7 297
7 298
7 299
7 300
7 301
7 302
7 303
7 304
7 305
7 306
7 307
7 308
7 309
7 310
7 311
7 312
7 320
7 321
7 322
7 323
7 324
7 325
7 326
7 327
7 328
7 328
7 329
7 329
7 330
7 330
7 331
7 331
7 332
7 332
7 333
7 334
7 334
7 335
7 335
7 336
7 336
7 337
7 337
7 338
7 338
7 339
7 340
7 341
7 342
7 343
7 344
7 345
7 346
7 347
7 348
7 349
7 350
7 351
7 352
7 353
7 354
7 355
7 356
7 357
7 358
7 359
7 360
7 361
7 362
7 363
7 364
7 365
7 366
7 367
7 368
7 369
7 370
7 371
7 373
7 374
7 375
7 376
7 377
7 378
7 379
7 380
7 381
7 382
7 383
7 384
7 385
7 387
7 388
7 389
7 390
7 391
7 391
7 392
7 392
7 393
7 393
7 394
7 394
7 395
7 395
7 396
7 397
7 398
7 398
7 399
7 400
7 401
7 401
7 402
7 402
7 403
7 404
7 405
7 405
7 406
7 407
7 407
7 408
7 408
7 409
7 409
7 410
7 410
7 411
7 411
7 412
7 413
7 413
7 414
7 415
7 416
7 417
7 417
7 418
7 419
7 420
7 421
7 423
7 424
7 426
7 427
7 428
7 429
7 430
7 430
7 431
7 431
7 433
7 434
7 434
7 435
7 435
7 436
7 436
7 437
7 43

9 329
9 329
9 330
9 330
9 331
9 331
9 332
9 332
9 333
9 334
9 334
9 335
9 335
9 336
9 336
9 337
9 337
9 338
9 338
9 339
9 340
9 341
9 342
9 343
9 344
9 345
9 346
9 347
9 348
9 349
9 350
9 351
9 352
9 353
9 354
9 355
9 356
9 357
9 358
9 359
9 360
9 361
9 362
9 363
9 364
9 365
9 366
9 367
9 368
9 369
9 370
9 371
9 373
9 374
9 375
9 376
9 377
9 378
9 379
9 380
9 381
9 382
9 383
9 384
9 385
9 387
9 388
9 389
9 390
9 391
9 391
9 392
9 392
9 393
9 393
9 394
9 394
9 395
9 395
9 396
9 397
9 398
9 398
9 399
9 400
9 401
9 401
9 402
9 402
9 403
9 404
9 405
9 405
9 406
9 407
9 407
9 408
9 408
9 409
9 409
9 410
9 410
9 411
9 411
9 412
9 413
9 413
9 414
9 415
9 416
9 417
9 417
9 418
9 419
9 420
9 421
9 423
9 424
9 426
9 427
9 428
9 429
9 430
9 430
9 431
9 431
9 433
9 434
9 434
9 435
9 435
9 436
9 436
9 437
9 439
9 439
9 440
9 441
9 441
9 442
9 443
9 443
9 444
9 444
9 445
9 445
9 446
9 446
9 447
9 447
9 448
9 448
9 449
9 449
9 450
9 451
9 451
9 452
9 452
9 453
9 454
9 456
9 456
9 457
9 458
9 460
9 46

...

607 609
607 609
607 610
607 611
607 611
607 613
607 614
607 615
607 616
607 617
607 619
607 621
607 622
607 623
607 624
607 625
607 626
607 627
607 628
607 629
607 630
607 631
607 632
607 633
607 634
607 637
607 638
607 639
607 640
607 643
607 644
607 646
607 647
607 651
607 653
607 654
607 657
607 662
607 663
607 666
607 667
607 668
607 670
607 676
607 678
607 679
607 682
607 684
607 686
607 687
607 688
607 689
607 690
607 691
607 693
607 694
607 701
607 702
607 705
607 706
607 711
607 715
607 716
607 717
607 720
607 721
607 722
607 723
607 725
607 726
607 729
607 730
607 731
607 733
607 740
607 741
607 744
607 746
607 746
607 747
607 747
607 748
607 748
607 749
607 750
607 750
607 751
607 752
607 753
607 754
607 754
607 755
607 755
607 756
607 756
607 757
607 758
607 758
607 759
607 759
607 760
607 760
607 761
607 761
607 762
608 609
608 609
608 610
608 611
608 611
608 613
608 614
608 615
608 616
608 617
608 619
608 621
608 622
608 623
608 624
608 625
608 626
608 627
608 628
608 629


617 679
617 682
617 684
617 686
617 687
617 688
617 689
617 690
617 691
617 693
617 694
617 701
617 702
617 705
617 706
617 711
617 715
617 716
617 717
617 720
617 721
617 722
617 723
617 725
617 726
617 729
617 730
617 731
617 733
617 740
617 741
617 744
617 746
617 746
617 747
617 747
617 748
617 748
617 749
617 750
617 750
617 751
617 752
617 753
617 754
617 754
617 755
617 755
617 756
617 756
617 757
617 758
617 758
617 759
617 759
617 760
617 760
617 761
617 761
617 762
619 621
619 622
619 623
619 624
619 625
619 626
619 627
619 628
619 629
619 630
619 631
619 632
619 633
619 634
619 637
619 638
619 639
619 640
619 643
619 644
619 646
619 647
619 651
619 653
619 654
619 657
619 662
619 663
619 666
619 667
619 668
619 670
619 676
619 678
619 679
619 682
619 684
619 686
619 687
619 688
619 689
619 690
619 691
619 693
619 694
619 701
619 702
619 705
619 706
619 711
619 715
619 716
619 717
619 720
619 721
619 722
619 723
619 725
619 726
619 729
619 730
619 731
619 733
619 740
619 741


632 733
632 740
632 741
632 744
632 746
632 746
632 747
632 747
632 748
632 748
632 749
632 750
632 750
632 751
632 752
632 753
632 754
632 754
632 755
632 755
632 756
632 756
632 757
632 758
632 758
632 759
632 759
632 760
632 760
632 761
632 761
632 762
633 634
633 637
633 638
633 639
633 640
633 643
633 644
633 646
633 647
633 651
633 653
633 654
633 657
633 662
633 663
633 666
633 667
633 668
633 670
633 676
633 678
633 679
633 682
633 684
633 686
633 687
633 688
633 689
633 690
633 691
633 693
633 694
633 701
633 702
633 705
633 706
633 711
633 715
633 716
633 717
633 720
633 721
633 722
633 723
633 725
633 726
633 729
633 730
633 731
633 733
633 740
633 741
633 744
633 746
633 746
633 747
633 747
633 748
633 748
633 749
633 750
633 750
633 751
633 752
633 753
633 754
633 754
633 755
633 755
633 756
633 756
633 757
633 758
633 758
633 759
633 759
633 760
633 760
633 761
633 761
633 762
634 637
634 638
634 639
634 640
634 643
634 644
634 646
634 647
634 651
634 653
634 654
634 657


666 730
666 731
666 733
666 740
666 741
666 744
666 746
666 746
666 747
666 747
666 748
666 748
666 749
666 750
666 750
666 751
666 752
666 753
666 754
666 754
666 755
666 755
666 756
666 756
666 757
666 758
666 758
666 759
666 759
666 760
666 760
666 761
666 761
666 762
667 668
667 670
667 676
667 678
667 679
667 682
667 684
667 686
667 687
667 688
667 689
667 690
667 691
667 693
667 694
667 701
667 702
667 705
667 706
667 711
667 715
667 716
667 717
667 720
667 721
667 722
667 723
667 725
667 726
667 729
667 730
667 731
667 733
667 740
667 741
667 744
667 746
667 746
667 747
667 747
667 748
667 748
667 749
667 750
667 750
667 751
667 752
667 753
667 754
667 754
667 755
667 755
667 756
667 756
667 757
667 758
667 758
667 759
667 759
667 760
667 760
667 761
667 761
667 762
668 670
668 676
668 678
668 679
668 682
668 684
668 686
668 687
668 688
668 689
668 690
668 691
668 693
668 694
668 701
668 702
668 705
668 706
668 711
668 715
668 716
668 717
668 720
668 721
668 722
668 723
668 725


705 750
705 751
705 752
705 753
705 754
705 754
705 755
705 755
705 756
705 756
705 757
705 758
705 758
705 759
705 759
705 760
705 760
705 761
705 761
705 762
706 711
706 715
706 716
706 717
706 720
706 721
706 722
706 723
706 725
706 726
706 729
706 730
706 731
706 733
706 740
706 741
706 744
706 746
706 746
706 747
706 747
706 748
706 748
706 749
706 750
706 750
706 751
706 752
706 753
706 754
706 754
706 755
706 755
706 756
706 756
706 757
706 758
706 758
706 759
706 759
706 760
706 760
706 761
706 761
706 762
711 715
711 716
711 717
711 720
711 721
711 722
711 723
711 725
711 726
711 729
711 730
711 731
711 733
711 740
711 741
711 744
711 746
711 746
711 747
711 747
711 748
711 748
711 749
711 750
711 750
711 751
711 752
711 753
711 754
711 754
711 755
711 755
711 756
711 756
711 757
711 758
711 758
711 759
711 759
711 760
711 760
711 761
711 761
711 762
715 716
715 717
715 720
715 721
715 722
715 723
715 725
715 726
715 729
715 730
715 731
715 733
715 740
715 741
715 744
715 746


In [25]:
len(consistent)

55

In [99]:
len(df_conflicts_details)

22

In [134]:
len(df_conflicts_details)

48

In [135]:
df_conflicts_details

ConnectivityHemisphere_link1 ConnectivityHemisphere_link2  \
0                            L                            L   
0                            R                            R   
0                            L                            L   
0                            R                            R   
0                            R                            R   
0                            R                            R   
0                            R                            R   
0                            L                            L   
0                            L                            L   
0                            L                            L   
0                            R                            R   
0                            R                            R   
0                            R                            R   
0                            L                            L   
0                            R                            R   
0                            R                            R   
0                            L                            L   
0                            R                            R   
0                            R                            R   
0                            R                            R   
0                            L                            L   
0                            L                            L   
0                            R                            R   
0                            R                            R   
0                            L                            L   
0                            R                            R   
0                            R                            R   
0                            L                            L   
0                            R                            R   
0                            L                            L   
0                            L                            L   
0                            L                            L   
0                            L                            L   
0                            L                            L   
0                            R                            R   
0                            L                            L   
0                            R                            R   
0                            L                            L   
0                            L                            L   
0                            R                            R   
0                            R                            R   
0                            R                            R   
0                            R                            R   
0                            L                            L   
0                            L                            L   
0                            R                            R   
0                            R                            R   
0                            L                            L   

                      ConnectivityNameHO_link1  \
0                                 Frontal Pole   
0                             Precentral Gyrus   
0                               Occipital Pole   
0                                 Frontal Pole   
0                                 Frontal Pole   
0                             Precentral Gyrus   
0                             Precentral Gyrus   
0  Lateral Occipital Cortex, superior division   
0                       Superior Frontal Gyrus   
0                       Superior Frontal Gyrus   
0                                 Frontal Pole   
0                                 Frontal Pole   
0                                 Frontal Pole   
0                             Precentral Gyrus   
0                            Precuneous Cortex   
0                            Precuneous Cortex   
0      Supramarginal Gyrus, posterior division   
0             

In [37]:
csvPath = 'csv_input/als.csv'

df = pd.read_csv(in_file)
columns_index_include = [0,1,28,29,30,31]

In [39]:
column_index

[4, 13, 17, 23, 27]

In [38]:

df.iloc[1:3,column_index]

PaperID.1 SeedHemisphere            SeedNameHO ConnectivityHemisphere  \
1         1              R        Insular Cortex                      L   
2         1              R  Middle Frontal Gyrus                      L   

                    ConnectivityNameHO  
1                         Frontal Pole  
2  Cingulate Gyrus, posterior division

In [18]:
df.iloc[1:3,[0,1]]

S_No  PaperID
1     2      1.0
2     3      1.0

In [ ]:
conflicts

In [ ]:
 df.loc[(df[df.columns[s_no_column_index].item()  ] == 174)]

In [ ]:
df.iloc[170:200,[1,17,27,32]]

In [ ]:
df[1:2].columns[paper_id_column_index[0]]

In [ ]:
k = df.columns[paper_id_column_index].item()

In [ ]:
k

In [ ]:
df.columns[paper_id_column_index].item() 

In [ ]:
df_extracted

In [ ]:
for ix1, row1 in  tqdm(df.iterrows()):
    print(row1[s_no_column_index])

In [ ]:
q = df[1:2]

In [ ]:
w = q[df.columns[[1,2]]]

In [ ]:
w.items()

In [ ]:
a.append([2])

In [ ]:
a